In [1]:
import h5py

In [2]:
h5_file = "/home/user/data/PHMbenchdata/PHM-Vibench/metadata_5_29.h5"
h5 = h5py.File(h5_file, 'r')
# analyze_hdf5_dataset(h5_file)

## single fix

In [3]:
h5_file = "/home/user/data/PHMbenchdata/PHM-Vibench/metadata_5_29.h5"
h5 = h5py.File(h5_file, 'r')
h6_file = "/home/user/data/PHMbenchdata/PHM-Vibench/metadata_6_1.h5"
h6 = h5py.File(h6_file, 'r')

In [4]:
id = '47064'
# h5[id],
h6[id]

<HDF5 dataset "47064": shape (512000, 6, 1), type "<f8">

In [5]:
len(h5), len(h6)

(49653, 49875)

In [24]:
# 统计h5文件并进行转换
conversion_results = []
output_file = "/home/user/data/PHMbenchdata/PHM-Vibench/metadata_6_1.h5"
import tqdm
import numpy as np
# 创建新的h5文件
with h5py.File(output_file, 'w') as new_h5:
    for key in tqdm.tqdm(h5.keys()):
        try:
            original_data = h5[key][()]
            original_shape = original_data.shape
            original_dtype = original_data.dtype
            
            # 转换数据类型为float
            converted_data = original_data.astype(np.float64)
            
            # 如果是3维，转换为2维 (L, C)
            if len(original_shape) == 3:
                # 假设3维数据格式为 (samples, length, channels) 或类似
                # 将其重塑为 (length, channels) 或 (L, C)
                if original_shape[-1] == 1:
                    # 如果第一维是1，去掉它
                    # new_shape = original_shape[1:]
                    converted_data = converted_data.reshape(original_shape[0], original_shape[1])  # 保持第一维不变，展平其他维度
                # else:
                #     # 将3维转为2维：合并前两维或根据具体需求调整
                    new_shape = (original_shape[0], original_shape[1])
                #     converted_data = converted_data.reshape(new_shape)
            else:
                new_shape = converted_data.shape
            
            # 保存到新文件
            new_h5.create_dataset(key, data=converted_data)
            
            # 记录转换结果
            conversion_results.append({
                'dataset_id': key,
                'original_shape': original_shape,
                'new_shape': new_shape,
                'original_dtype': str(original_dtype),
                'new_dtype': str(converted_data.dtype),
                'conversion_type': '3D to 2D' if len(original_shape) == 3 else 'dtype only',
                'status': 'success'
            })
            
        except Exception as e:
            conversion_results.append({
                'dataset_id': key,
                'original_shape': 'error',
                'new_shape': 'error',
                'original_dtype': 'error',
                'new_dtype': 'error',
                'conversion_type': 'error',
                'status': f'failed: {str(e)}'
            })

# 创建转换结果表格
conversion_df = pd.DataFrame(conversion_results)
print("数据转换结果:")
print(conversion_df)

# 保存转换结果到CSV
conversion_df.to_csv("conversion_summary.csv", index=False)
print(f"\n转换完成！新文件已保存为: {output_file}")
print("转换结果已保存到: conversion_summary.csv")

  0%|          | 0/49653 [00:00<?, ?it/s]

100%|██████████| 49653/49653 [03:32<00:00, 234.17it/s] 


数据转换结果:
      dataset_id  original_shape    new_shape original_dtype new_dtype  \
0              1  (243938, 2, 1)  (243938, 2)        float64   float64   
1             10  (486224, 2, 1)  (486224, 2)        float64   float64   
2            100  (484483, 2, 1)  (484483, 2)        float64   float64   
3           1000   (32768, 2, 1)   (32768, 2)        float64   float64   
4          10000    (2560, 2, 1)    (2560, 2)        float64   float64   
...          ...             ...          ...            ...       ...   
49648       9995    (2560, 2, 1)    (2560, 2)        float64   float64   
49649       9996    (2560, 2, 1)    (2560, 2)        float64   float64   
49650       9997    (2560, 2, 1)    (2560, 2)        float64   float64   
49651       9998    (2560, 2, 1)    (2560, 2)        float64   float64   
49652       9999    (2560, 2, 1)    (2560, 2)        float64   float64   

      conversion_type   status  
0            3D to 2D  success  
1            3D to 2D  success  
2   